In [6]:
!pip install transformers -U

Defaulting to user installation because normal site-packages is not writeable
  Using cached transformers-4.36.1-py3-none-any.whl (8.3 MB)
  Attempting uninstall: transformers
    Found existing installation: transformers 4.29.2
    Uninstalling transformers-4.29.2:
      Successfully uninstalled transformers-4.29.2
  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
optimum-graphcore 0.7.1 requires transformers==4.29.2, but you have transformers 4.36.1 which is incompatible.


In [1]:
import os 
os.chdir('/work/jh2lab')

In [2]:
os.getcwd()

'/work/jh2lab'

In [3]:
from huggingface_hub import notebook_login

notebook_login()

In [4]:
from datasets import load_dataset
tail = '_10'
dataset = load_dataset('audiofolder', data_dir="/work/jh2lab/elic_model/cr_audio_chunk" + tail, split = 'train')


Resolving data files:   0%|          | 0/1838 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

In [5]:
dataset = dataset.train_test_split(test_size=0.2)
dataset

DatasetDict({
    train: Dataset({
        features: ['audio', 'transcription'],
        num_rows: 1469
    })
    test: Dataset({
        features: ['audio', 'transcription'],
        num_rows: 368
    })
})

In [6]:
from datasets import Audio

dataset = dataset.cast_column("audio", Audio(sampling_rate=16000))

In [7]:
dataset

DatasetDict({
    train: Dataset({
        features: ['audio', 'transcription'],
        num_rows: 1469
    })
    test: Dataset({
        features: ['audio', 'transcription'],
        num_rows: 368
    })
})

In [6]:
#dataset['train'][0]

In [8]:

# data augmentation
from audiomentations import Compose, AddGaussianNoise, TimeStretch, PitchShift, Shift

augment_waveform = Compose([
    AddGaussianNoise(min_amplitude=0.005, max_amplitude=0.015, p=0.2),
    TimeStretch(min_rate=0.8, max_rate=1.25, p=0.2, leave_length_unchanged=False),
    PitchShift(min_semitones=-4, max_semitones=4, p=0.2)
    ,])


def augment_dataset(batch):

    audio = batch["audio"]["array"]
    # apply augmentation
    augmented_audio = augment_waveform(samples=audio, sample_rate=16000)

    batch["audio"]["array"] = augmented_audio


    return batch


In [9]:
dataset["train"] = dataset["train"].map(augment_dataset)


Map:   0%|          | 0/1469 [00:00<?, ? examples/s]

/home/sz38235/.local/lib/python3.11/site-packages/audiomentations/core/transforms_interface.py:62: UserWarning: Warning: input samples dtype is np.float64. Converting to np.float32
  warnings.warn(
/home/sz38235/.local/lib/python3.11/site-packages/audiomentations/core/transforms_interface.py:62: UserWarning: Warning: input samples dtype is np.float64. Converting to np.float32
  warnings.warn(


In [10]:
dataset["test"] = dataset["test"].map(augment_dataset)

Map:   0%|          | 0/368 [00:00<?, ? examples/s]

In [11]:
from transformers import WhisperFeatureExtractor

#feature_extractor = WhisperFeatureExtractor.from_pretrained("openai/whisper-large-v3")


feature_extractor = WhisperFeatureExtractor.from_pretrained("openai/whisper-large-v3", language="croatian", task="transcribe")


In [12]:
from transformers import WhisperTokenizer

tokenizer = WhisperTokenizer.from_pretrained("openai/whisper-large-v3", language="croatian", task="transcribe")


Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [13]:
from transformers import WhisperProcessor

processor = WhisperProcessor.from_pretrained("openai/whisper-large-v3", language="croatian", task="transcribe")


Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [14]:
def prepare_dataset(batch):
    # load and resample audio data from 48 to 16kHz
    audio = batch["audio"]

    # compute log-Mel input features from input audio array 
    batch["input_features"] = feature_extractor(audio["array"], sampling_rate=audio["sampling_rate"]).input_features[0]

    # encode target text to label ids 
    batch["labels"] = tokenizer(batch["transcription"], max_length=225, truncation=True).input_ids
    return batch



In [15]:
dataset["train"] = dataset["train"].map(prepare_dataset)


Map:   0%|          | 0/1469 [00:00<?, ? examples/s]

2024-03-22 10:25:27.310864: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-03-22 10:25:27.310925: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-03-22 10:25:27.522018: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-03-22 10:25:28.067232: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-03-22 10:25:34.950754: W tensorflow/compiler/tf2

In [16]:
dataset["test"] = dataset["test"].map(prepare_dataset)

Map:   0%|          | 0/368 [00:00<?, ? examples/s]

In [17]:
dataset

DatasetDict({
    train: Dataset({
        features: ['audio', 'transcription', 'input_features', 'labels'],
        num_rows: 1469
    })
    test: Dataset({
        features: ['audio', 'transcription', 'input_features', 'labels'],
        num_rows: 368
    })
})

In [18]:
dataset.save_to_disk("/work/jh2lab/elic_model/ckm_dataset_preprocessed" + tail)

Saving the dataset (0/6 shards):   0%|          | 0/1469 [00:00<?, ? examples/s]

Saving the dataset (0/2 shards):   0%|          | 0/368 [00:00<?, ? examples/s]

In [13]:
#dataset['train'][-1]

{'audio': {'path': None,
  'array': array([0.00119019, 0.00387573, 0.00088501, ..., 0.00610352, 0.00906372,
         0.01098633]),
  'sampling_rate': 16000},
 'transcription': "Kat san bila veća onda san š njun delala, ko dite bin samo bila gjedala i više @ gluposti storila leh ča njoj pomogla, ali ipak evo to mi j' ostalo va glavi.  I Telovo meni j Telovo vavik bilo lipo i posebno  jer smo mi ko dica, ženska dica, su vavik bila va belon obučena. I mićera i vela i vele divojke dok se nisu oženile.",
 'input_features': [[-0.30792319774627686,
   0.17268431186676025,
   0.22991222143173218,
   0.09973514080047607,
   0.029380202293395996,
   0.29307734966278076,
   0.13330739736557007,
   0.24445700645446777,
   0.08647400140762329,
   -0.06272542476654053,
   0.11647611856460571,
   0.21770191192626953,
   0.16695719957351685,
   0.03597557544708252,
   -0.08976316452026367,
   -0.16813015937805176,
   -0.08644747734069824,
   0.21871811151504517,
   0.17780739068984985,
   0.1665297150

In [19]:
import os
os.environ["CUDA_VISIBLE_DEVICES"] = "1"

In [20]:
from datasets import load_from_disk
dataset = load_from_disk("/work/jh2lab/elic_model/ckm_dataset_preprocessed" + tail)

In [21]:
#import wandb
import pandas as pd

In [22]:
import torch

from dataclasses import dataclass
from typing import Any, Dict, List, Union

@dataclass
class DataCollatorSpeechSeq2SeqWithPadding:
    processor: Any

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        # split inputs and labels since they have to be of different lengths and need different padding methods
        # first treat the audio inputs by simply returning torch tensors
        input_features = [{"input_features": feature["input_features"]} for feature in features]
        batch = self.processor.feature_extractor.pad(input_features, return_tensors="pt")

        # get the tokenized label sequences
        label_features = [{"input_ids": feature["labels"]} for feature in features]
        # pad the labels to max length
        labels_batch = self.processor.tokenizer.pad(label_features, return_tensors="pt")

        # replace padding with -100 to ignore loss correctly
        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

        # if bos token is appended in previous tokenization step,
        # cut bos token here as it's append later anyways
        if (labels[:, 0] == self.processor.tokenizer.bos_token_id).all().cpu().item():
            labels = labels[:, 1:]

        batch["labels"] = labels

        return batch


In [23]:
data_collator = DataCollatorSpeechSeq2SeqWithPadding(processor=processor)

In [24]:
import evaluate

metric = evaluate.load("wer")


In [25]:
def compute_metrics(pred):
    pred_ids = pred.predictions
    label_ids = pred.label_ids

    # replace -100 with the pad_token_id
    label_ids[label_ids == -100] = tokenizer.pad_token_id

    # we do not want to group tokens when computing the metrics
    pred_str = tokenizer.batch_decode(pred_ids, skip_special_tokens=True)
    label_str = tokenizer.batch_decode(label_ids, skip_special_tokens=True)

    wer = 100 * metric.compute(predictions=pred_str, references=label_str)

    return {"wer": wer}


In [26]:
from transformers import WhisperForConditionalGeneration

model = WhisperForConditionalGeneration.from_pretrained("openai/whisper-large-v3")


In [27]:
model.config.forced_decoder_ids = None
model.config.suppress_tokens = []

In [28]:
print("./whisper-large-v3-croarian" + tail)

./whisper-large-v3-croarian_10


In [29]:
from transformers import Seq2SeqTrainingArguments

training_args = Seq2SeqTrainingArguments(
    output_dir="/work/jh2lab/elic_model/whisper-large-v3-croarian" + tail,  # v2 add white noise and trunk
    per_device_train_batch_size=16,
    gradient_accumulation_steps=1,  # increase by 2x for every 2x decrease in batch size
    learning_rate=1e-5,
    warmup_steps=500,
    max_steps=4000,
    gradient_checkpointing=True,
    fp16=True,
    evaluation_strategy="steps",
    per_device_eval_batch_size=8,
    predict_with_generate=True,
    generation_max_length=225,
    save_steps=1000,
    eval_steps=1000,
    logging_steps=25,
    report_to=["tensorboard"],
    load_best_model_at_end=True,
    metric_for_best_model="wer",
    greater_is_better=False,
    push_to_hub=False,
)


In [30]:
from transformers import Seq2SeqTrainer

trainer = Seq2SeqTrainer(
    args=training_args,
    model=model,
    train_dataset=dataset["train"],
    eval_dataset=dataset["test"],
    data_collator=data_collator,
    compute_metrics=compute_metrics,
    tokenizer=processor.feature_extractor,
)


Detected kernel version 4.18.0, which is below the recommended minimum of 5.5.0; this can cause the process to hang. It is recommended to upgrade the kernel to the minimum version or higher.


In [76]:
#trainer.train(resume_from_checkpoint=True)

There were missing keys in the checkpoint model loaded: ['proj_out.weight'].
/home/sz38235/.local/lib/python3.11/site-packages/torch/utils/checkpoint.py:460: UserWarning: torch.utils.checkpoint: please pass in use_reentrant=True or use_reentrant=False explicitly. The default value of use_reentrant will be updated to be False in the future. To maintain current behavior, pass use_reentrant=True. It is recommended that you use use_reentrant=False. Refer to docs for more details on the differences between the two variants.
  warnings.warn(


Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'max_length': 448, 'suppress_tokens': [], 'begin_suppress_tokens': [220, 50257]}
/home/sz38235/.local/lib/python3.11/site-packages/torch/utils/checkpoint.py:460: UserWarning: torch.utils.checkpoint: please pass in use_reentrant=True or use_reentrant=False explicitly. The default value of use_reentrant will be updated to be False in the future. To maintain current behavior, pass use_reentrant=True. It is recommended that you use use_reentrant=False. Refer to docs for more details on the differences between the two variants.
  warnings.warn(
Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://hugging

TrainOutput(global_step=4000, training_loss=0.0008440194092690944, metrics={'train_runtime': 7216.7289, 'train_samples_per_second': 8.868, 'train_steps_per_second': 0.554, 'total_flos': 2.1700501183660032e+20, 'train_loss': 0.0008440194092690944, 'epoch': 80.0})

In [31]:
trainer.train()

/home/sz38235/.local/lib/python3.11/site-packages/torch/utils/checkpoint.py:460: UserWarning: torch.utils.checkpoint: please pass in use_reentrant=True or use_reentrant=False explicitly. The default value of use_reentrant will be updated to be False in the future. To maintain current behavior, pass use_reentrant=True. It is recommended that you use use_reentrant=False. Refer to docs for more details on the differences between the two variants.
  warnings.warn(
`use_cache = True` is incompatible with gradient checkpointing. Setting `use_cache = False`...


Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'max_length': 448, 'suppress_tokens': [], 'begin_suppress_tokens': [220, 50257]}
/home/sz38235/.local/lib/python3.11/site-packages/torch/utils/checkpoint.py:460: UserWarning: torch.utils.checkpoint: please pass in use_reentrant=True or use_reentrant=False explicitly. The default value of use_reentrant will be updated to be False in the future. To maintain current behavior, pass use_reentrant=True. It is recommended that you use use_reentrant=False. Refer to docs for more details on the differences between the two variants.
  warnings.warn(
Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://hugging

TrainOutput(global_step=4000, training_loss=0.21308091940172016, metrics={'train_runtime': 14751.4562, 'train_samples_per_second': 4.339, 'train_steps_per_second': 0.271, 'total_flos': 2.1700161433829376e+20, 'train_loss': 0.21308091940172016, 'epoch': 43.48})

In [32]:
kwargs = {
    #"dataset_tags": "mozilla-foundation/common_voice_11_0",
    #"dataset": "Common Voice 11.0",  # a 'pretty' name for the training dataset
    "dataset_args": "config: cr, split: test",
    "language": "cr",
    #"model_name": "Whisper Small Hi - Sanchit Gandhi",  # a 'pretty' name for your model
    "finetuned_from": "openai/whisper-large-v3",
    "tasks": "automatic-speech-recognition",
    #"tags": "hf-asr-leaderboard",
}

In [33]:
trainer.push_to_hub(**kwargs)

Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'max_length': 448, 'suppress_tokens': [], 'begin_suppress_tokens': [220, 50257]}


events.out.tfevents.1711118199.b6-1.1404739.0:   0%|          | 0.00/32.0k [00:00<?, ?B/s]

training_args.bin:   0%|          | 0.00/4.92k [00:00<?, ?B/s]

model-00002-of-00002.safetensors:   0%|          | 0.00/1.18G [00:00<?, ?B/s]

Upload 4 LFS files:   0%|          | 0/4 [00:00<?, ?it/s]

model-00001-of-00002.safetensors:   0%|          | 0.00/4.99G [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/ninninz/whisper-large-v3-croarian_10/commit/f26d99972bc43c5ffd5a8ce4c8b2c10feca0ce76', commit_message='End of training', commit_description='', oid='f26d99972bc43c5ffd5a8ce4c8b2c10feca0ce76', pr_url=None, pr_revision=None, pr_num=None)

In [34]:
tokenizer.save_pretrained("/work/jh2lab/elic_model/whisper-large-v3-croarian" + tail) # add this to the folder, it is not auto saved

('/work/jh2lab/elic_model/whisper-large-v3-croarian_10/tokenizer_config.json',
 '/work/jh2lab/elic_model/whisper-large-v3-croarian_10/special_tokens_map.json',
 '/work/jh2lab/elic_model/whisper-large-v3-croarian_10/vocab.json',
 '/work/jh2lab/elic_model/whisper-large-v3-croarian_10/merges.txt',
 '/work/jh2lab/elic_model/whisper-large-v3-croarian_10/normalizer.json',
 '/work/jh2lab/elic_model/whisper-large-v3-croarian_10/added_tokens.json')

In [35]:
trainer.push_to_hub("ninninz/whisper-large-v3-croatian" + tail)

Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'max_length': 448, 'suppress_tokens': [], 'begin_suppress_tokens': [220, 50257]}


CommitInfo(commit_url='https://huggingface.co/ninninz/whisper-large-v3-croarian_10/commit/4f1c34d1018c98c6472f2486a89e343837d9eaa4', commit_message='ninninz/whisper-large-v3-croatian_10', commit_description='', oid='4f1c34d1018c98c6472f2486a89e343837d9eaa4', pr_url=None, pr_revision=None, pr_num=None)